# DAEDRA: Determining Adverse Event Disposition for Regulatory Affairs

DAEDRA is a language model intended to predict the disposition (outcome) of an adverse event based on the text of the event report. Intended to be used to classify reports in passive reporting systems, it is trained on the [VAERS](https://vaers.hhs.gov/) dataset, which contains reports of adverse events following vaccination in the United States.

In [1]:
# %pip install accelerate -U

Note: you may need to restart the kernel to use updated packages.


In [2]:
# %pip install transformers datasets shap watermark wandb

Note: you may need to restart the kernel to use updated packages.


In [66]:
import pandas as pd
import numpy as np
import torch
import os
from typing import List
from sklearn.metrics import f1_score, accuracy_score, classification_report
from transformers import AutoTokenizer, Trainer, AutoModelForSequenceClassification, TrainingArguments, pipeline
from datasets import load_dataset, Dataset, DatasetDict
from pyarrow import Table
import shap
import wandb

os.environ["TOKENIZERS_PARALLELISM"] = "false"

%load_ext watermark

The watermark extension is already loaded. To reload it, use:
  %reload_ext watermark


In [43]:
device: str = 'cuda' if torch.cuda.is_available() else 'cpu'

SEED: int = 42

BATCH_SIZE: int = 32
EPOCHS: int = 3
model_ckpt: str = "distilbert-base-uncased"

CLASS_NAMES: List[str] = ["DIED",
                          "ER_VISIT",
                          "HOSPITAL",
                          "OFC_VISIT",
                          #"X_STAY",      # pruned
                          #"DISABLE",     # pruned
                          #"D_PRESENTED"  # pruned
                          ]




# WandB configuration
os.environ["WANDB_PROJECT"] = "DAEDRA model training"  # name your W&B project
os.environ["WANDB_LOG_MODEL"] = "checkpoint"  # log all model checkpoints
os.environ["WANDB_NOTEBOOK_NAME"] = "DAEDRA.ipynb"

In [44]:
%watermark --iversion

shap   : 0.44.1
torch  : 1.12.0
logging: 0.5.1.2
numpy  : 1.23.5
pandas : 2.0.2
re     : 2.2.1



In [45]:
!nvidia-smi

Sun Jan 28 13:54:22 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.129.03             Driver Version: 535.129.03   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla V100-PCIE-16GB           Off | 00000001:00:00.0 Off |                  Off |
| N/A   30C    P0              38W / 250W |  12830MiB / 16384MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

## Loading the data set

In [46]:
dataset = load_dataset("chrisvoncsefalvay/vaers-outcomes")

In [47]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'text', 'labels'],
        num_rows: 1270444
    })
    test: Dataset({
        features: ['id', 'text', 'labels'],
        num_rows: 272238
    })
    val: Dataset({
        features: ['id', 'text', 'labels'],
        num_rows: 272238
    })
})

In [70]:
SUBSAMPLING: float = 0.1

In [48]:
def minisample(ds: DatasetDict, fraction: float) -> DatasetDict:
    res = DatasetDict()

    res["train"] = Dataset.from_dict(ds["train"].shuffle()[:round(len(ds["train"]) * fraction)])
    res["test"] = Dataset.from_dict(ds["test"].shuffle()[:round(len(ds["test"]) * fraction)])
    res["val"] = Dataset.from_dict(ds["val"].shuffle()[:round(len(ds["val"]) * fraction)])
    
    return res

In [49]:
dataset = minisample(dataset, SUBSAMPLING)

In [50]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'text', 'labels'],
        num_rows: 127044
    })
    test: Dataset({
        features: ['id', 'text', 'labels'],
        num_rows: 27224
    })
    val: Dataset({
        features: ['id', 'text', 'labels'],
        num_rows: 27224
    })
})

We prune things down to the first four keys: `DIED`, `ER_VISIT`, `HOSPITAL`, `OFC_VISIT`.

In [51]:
ds = DatasetDict()

for i in ["test", "train", "val"]:
    tab = Table.from_arrays([dataset[i]["id"], dataset[i]["text"], [i[:4] for i in dataset[i]["labels"]]], names=["id", "text", "labels"])
    ds[i] = Dataset(tab)

dataset = ds

### Tokenisation and encoding

In [52]:
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

In [53]:
def tokenize_and_encode(examples):
  return tokenizer(examples["text"], truncation=True)

In [54]:
cols = dataset["train"].column_names
cols.remove("labels")
ds_enc = dataset.map(tokenize_and_encode, batched=True, remove_columns=cols)

Map: 100%|██████████| 27224/27224 [00:11<00:00, 2376.02 examples/s]


### Training

In [55]:
class MultiLabelTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False):
        labels = inputs.pop("labels")
        outputs = model(**inputs)
        logits = outputs.logits
        loss_fct = torch.nn.BCEWithLogitsLoss()
        loss = loss_fct(logits.view(-1, self.model.config.num_labels),
                        labels.float().view(-1, self.model.config.num_labels))
        return (loss, outputs) if return_outputs else loss

In [56]:
model = AutoModelForSequenceClassification.from_pretrained(model_ckpt, num_labels=len(CLASS_NAMES)).to("cuda")

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [57]:
def accuracy_threshold(y_pred, y_true, threshold=.5, sigmoid=True):
    y_pred = torch.from_numpy(y_pred)
    y_true = torch.from_numpy(y_true)

    if sigmoid:
        y_pred = y_pred.sigmoid()

    return ((y_pred > threshold) == y_true.bool()).float().mean().item()

In [58]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    return {'accuracy_thresh': accuracy_threshold(predictions, labels)}

In [63]:
args = TrainingArguments(
    output_dir="vaers",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=BATCH_SIZE,
    per_device_eval_batch_size=BATCH_SIZE,
    num_train_epochs=EPOCHS,
    weight_decay=.01,
    logging_steps=1,
    run_name=f"daedra-training",
    report_to=["wandb"]
)

In [64]:
multi_label_trainer = MultiLabelTrainer(
    model, 
    args, 
    train_dataset=ds_enc["train"], 
    eval_dataset=ds_enc["test"], 
    compute_metrics=compute_metrics, 
    tokenizer=tokenizer
)

In [71]:
if SUBSAMPLING != 1.0:
    wandb_tag: List[str] = [f"subsample-{SUBSAMPLING}"]
else:
    wandb_tag: List[str] = [f"full_sample"]
    
wandb.init(name="init_evaluation_run", tags=wandb_tag, magic=True)

multi_label_trainer.evaluate()
wandb.finish()

wandb: WARNING wandb.init() arguments ignored because wandb magic has already been initialized


In [62]:
if SUBSAMPLING != 1.0:
    wandb_tag: List[str] = [f"subsample-{SUBSAMPLING}"]
else:
    wandb_tag: List[str] = [f"full_sample"]
    
wandb.init(name="daedra_training_run", tags=wandb_tag, magic=True)

multi_label_trainer.train()
wandb.finish()

RuntimeError: Caught RuntimeError in replica 0 on device 0.
Original Traceback (most recent call last):
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/torch/nn/parallel/parallel_apply.py", line 61, in _worker
    output = module(*input, **kwargs)
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1130, in _call_impl
    return forward_call(*input, **kwargs)
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/transformers/models/distilbert/modeling_distilbert.py", line 1002, in forward
    distilbert_output = self.distilbert(
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/torch/nn/modules/module.py", line 1130, in _call_impl
    return forward_call(*input, **kwargs)
  File "/anaconda/envs/azureml_py38_PT_TF/lib/python3.8/site-packages/transformers/models/distilbert/modeling_distilbert.py", line 822, in forward
    return self.transformer(
  File "/anaconda/envs/azureml_py

### Evaluation

We instantiate a classifier `pipeline` and push it to CUDA.

In [ ]:
classifier = pipeline("text-classification", 
                      model, 
                      tokenizer=tokenizer, 
                      device="cuda:0")

We use the same tokenizer used for training to tokenize/encode the validation set.

In [ ]:
test_encodings = tokenizer.batch_encode_plus(dataset["val"]["text"], 
                                             max_length=None, 
                                             padding='max_length', 
                                             return_token_type_ids=True, 
                                             truncation=True)

Once we've made the data loadable by putting it into a `DataLoader`, we 

In [ ]:
test_data = torch.utils.data.TensorDataset(torch.tensor(test_encodings['input_ids']), 
                                           torch.tensor(test_encodings['attention_mask']), 
                                           torch.tensor(ds_enc["val"]["labels"]), 
                                           torch.tensor(test_encodings['token_type_ids']))
test_dataloader = torch.utils.data.DataLoader(test_data, 
                                              sampler=torch.utils.data.SequentialSampler(test_data), 
                                              batch_size=BATCH_SIZE)

In [ ]:
model.eval()

logit_preds, true_labels, pred_labels, tokenized_texts = [], [], [], []

for i, batch in enumerate(test_dataloader):
  batch = tuple(t.to(device) for t in batch)
  
  # Unpack the inputs from our dataloader
  b_input_ids, b_input_mask, b_labels, b_token_types = batch
  
  with torch.no_grad():
    outs = model(b_input_ids, attention_mask=b_input_mask)
    b_logit_pred = outs[0]
    pred_label = torch.sigmoid(b_logit_pred)

    b_logit_pred = b_logit_pred.detach().cpu().numpy()
    pred_label = pred_label.to('cpu').numpy()
    b_labels = b_labels.to('cpu').numpy()

  tokenized_texts.append(b_input_ids)
  logit_preds.append(b_logit_pred)
  true_labels.append(b_labels)
  pred_labels.append(pred_label)

# Flatten outputs
tokenized_texts = [item for sublist in tokenized_texts for item in sublist]
pred_labels = [item for sublist in pred_labels for item in sublist]
true_labels = [item for sublist in true_labels for item in sublist]

# Converting flattened binary values to boolean values
true_bools = [tl == 1 for tl in true_labels]
pred_bools = [pl > 0.50 for pl in pred_labels] 

We create a classification report:

In [ ]:
print('Test F1 Accuracy: ', f1_score(true_bools, pred_bools, average='micro'))
print('Test Flat Accuracy: ', accuracy_score(true_bools, pred_bools), '\n')
clf_report = classification_report(true_bools, pred_bools, target_names=CLASS_NAMES)
print(clf_report)

Finally, we render a 'head to head' comparison table that maps each text prediction to actual and predicted labels.

In [ ]:
# Creating a map of class names from class numbers
idx2label = dict(zip(range(len(CLASS_NAMES)), CLASS_NAMES))

In [ ]:
true_label_idxs, pred_label_idxs = [], []

for vals in true_bools:
  true_label_idxs.append(np.where(vals)[0].flatten().tolist())
for vals in pred_bools:
  pred_label_idxs.append(np.where(vals)[0].flatten().tolist())

In [ ]:
true_label_texts, pred_label_texts = [], []

for vals in true_label_idxs:
  if vals:
    true_label_texts.append([idx2label[val] for val in vals])
  else:
    true_label_texts.append(vals)

for vals in pred_label_idxs:
  if vals:
    pred_label_texts.append([idx2label[val] for val in vals])
  else:
    pred_label_texts.append(vals)

In [ ]:
symptom_texts = [tokenizer.decode(text,
                                  skip_special_tokens=True,
                                  clean_up_tokenization_spaces=False) for text in tokenized_texts]

In [ ]:
comparisons_df = pd.DataFrame({'symptom_text': symptom_texts, 
                               'true_labels': true_label_texts, 
                               'pred_labels':pred_label_texts})
comparisons_df.to_csv('comparisons.csv')
comparisons_df

### Shapley analysis

In [ ]:
explainer = shap.Explainer(classifier, output_names=CLASS_NAMES)

#### Sampling correct predictions

First, let's look at some correct predictions of deaths:

In [ ]:
correct_death_predictions = comparisons_df[comparisons_df['true_labels'].astype(str) == "['DIED']"]

In [ ]:
texts = [i[:512] for i in correct_death_predictions.sample(n=6).symptom_text]
idxs = [i for i in range(len(texts))]

d_s = Dataset(Table.from_arrays([idxs, texts], names=["idx", "texts"]))

In [ ]:
shap_values = explainer(d_s["texts"])

In [ ]:
shap.plots.text(shap_values)